<a href="https://cognitiveclass.ai"><img src = "https://ibm.box.com/shared/static/9gegpsmnsoo25ikkbl4qzlvlyjbgxs5x.png" width = 400> </a>

<h1 align=center><font size = 5>Final Project: Silicon Valley Neighborhood Research</font></h1>

### Introduction
This project is to investigate Silicon Valley Neighborhood based on FourSquare API and clustering data science method

### Set up Environment

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
#from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
import csv
import time

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
#import folium # map rendering library

### Download the data from data.gov & Convert raw data into pd.DataFrame

In [2]:
url = 'https://data.sfgov.org/api/views/f9wk-m4qb/rows.csv?accessType=DOWNLOAD'
raw_data = pd.read_csv(url)
data = raw_data

### **Part 1 Reform DataFrame

In [3]:
# Need to switch 'the_geom' into [latitude, longitude]; create area center as in 'latitude' and 'longitude' columns
import re
def extractFloat(temp):
    output = re.findall(r"[-+]?\d*\.\d+|\d+", temp)
    output = [float(i) for i in output]
    return output
    
geo = data["the_geom"].str.split("MULTIPOLYGON", n = 1, expand = True)[1] 
latitude  = []
longitude = []
for j in range(len(geo)):
    lat  = []
    long = []
    lat  = extractFloat(geo[j])[1::2]
    long = extractFloat(geo[j])[0::2]
    latitude.append(np.array(lat).mean())
    longitude.append(np.array(long).mean())

data['latitude']  = latitude
data['longitude'] = longitude
data = data[data['PO_NAME'] != 'TRAVIS AFB']
city_ls           = data.PO_NAME.unique().tolist()

In [4]:
# Area List by City Name
area_ls = data.groupby('PO_NAME').sum()['Area__']

In [5]:
urlSJ  = 'https://public.opendatasoft.com/explore/dataset/us-zip-code-latitude-and-longitude/download/?format=csv&q=San+Jose+CA&timezone=America/Los_Angeles&use_labels_for_header=true'
dataSJ = pd.read_csv(urlSJ,sep=';')
dataSJ = dataSJ.rename(columns={"Zip": "ZIP", "Latitude": "latitude","Longitude":'longitude','City':'PO_NAME','State':'STATE'})
dataSJ['PO_NAME'] = dataSJ['PO_NAME'].str.upper()
dataSJ = dataSJ.drop(["Timezone", "Daylight savings time flag", "geopoint"], axis=1)
#dataSJ.head()
data   = data.append(dataSJ, ignore_index=True, sort=False)

santaclara = ['SANTA CLARA','NA',95051,'CA','NA','NA',37.3541, -121.9552]
cupertino  = ['CUPERTINO','NA',95014,'CA','NA','NA',37.3230, -122.0322]
campbell   = ['CAMPBELL','NA',95008,'CA','NA','NA',37.2872, -121.9500]
dataex     = pd.DataFrame([santaclara,cupertino,campbell], columns=data.columns)  
data       = data.append(dataex, ignore_index=True, sort=False)
data.drop_duplicates(subset ="ZIP", keep = False, inplace = True)
print("There are {} unique cities found in Greater San Francisco Bay Area.".format(len(data.PO_NAME.unique())))
data.head()

There are 99 unique cities found in Greater San Francisco Bay Area.


PO_NAME                                           the_geom    ZIP STATE  \
0       NAPA  MULTIPOLYGON (((-122.10329200180091 38.5132829...  94558    CA   
1  FAIRFIELD  MULTIPOLYGON (((-121.947475002335 38.301511000...  94533    CA   
2      DIXON  MULTIPOLYGON (((-121.65335500334429 38.3133870...  95620    CA   
3     SONOMA  MULTIPOLYGON (((-122.406843003057 38.155681999...  95476    CA   
4       NAPA  MULTIPOLYGON (((-122.29368500225117 38.1552379...  94559    CA   

        Area__ Length__   latitude   longitude  
0  1.23133e+10   995176  38.410697 -122.298535  
1  9.91786e+08   200773  38.279137 -122.025948  
2  7.23695e+09   441860  38.434585 -121.781528  
3  3.00141e+09   311319  38.279666 -122.456603  
4   1.1943e+09   359105  38.266265 -122.311414

### **Part 2 Access to Foursqaure database

In [6]:
# Input Foursquare ID/Secret/Version
CLIENT_ID = 'TJ0SPQOHXOF5CJGO2BUHJM2ZXXEJK3K1WQZZWG2Y23XZN025' # your Foursquare ID
CLIENT_SECRET = 'NQEXK1ULW5FOTFHEOROXCF4U1VELGW4N2GAD4IYNDET0VIKI' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)


Your credentails:
CLIENT_ID: TJ0SPQOHXOF5CJGO2BUHJM2ZXXEJK3K1WQZZWG2Y23XZN025
CLIENT_SECRET:NQEXK1ULW5FOTFHEOROXCF4U1VELGW4N2GAD4IYNDET0VIKI


In [7]:
# Test Run by only using the first row input
# Get neighborhood Data
bay_latitude = data.loc[0, 'latitude'] # neighborhood latitude value
bay_longitude = data.loc[0, 'longitude'] # neighborhood longitude value

bay_name = data.loc[0, 'PO_NAME'] # neighborhood name

print('Latitude and longitude values of first row "{}" are ({}, {}).'.format(bay_name, 
                                                               bay_latitude, 
                                                               bay_longitude))

LIMIT  = 20 # limit of number of venues returned by Foursquare API
radius = 10000 # define radius
price  = 2

# create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&price={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    bay_latitude, 
    bay_longitude, 
    radius,
    price,
    LIMIT)
url # display URL
results = requests.get(url).json()
#results

Latitude and longitude values of first row "NAPA" are (38.41069666247486, -122.29853512315688).


In [8]:
# Function that extracts the category of the venue
LIMIT        = 20
radius_range = 10000

def getNearbyVenues(names, latitudes, longitudes, radius=radius_range):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Location', 
                  'City Latitude', 
                  'City Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Category']
    
    return(nearby_venues)

In [9]:
bay_venues = getNearbyVenues(names=data['PO_NAME'],
                             latitudes=data['latitude'],
                             longitudes=data['longitude']
                            )

print("Bay Area Venues shape: {}".format(bay_venues.shape))
bay_venues.head(20)

NAPA
FAIRFIELD
DIXON
SONOMA
NAPA
PETALUMA
RIO VISTA
AMERICAN CANYON
NOVATO
NOVATO
BIRDS LANDING
VALLEJO
BENICIA
VALLEJO
VALLEJO
NOVATO
VALLEJO
NICASIO
OAKLEY
CROCKETT
PORT COSTA
SUISUN CITY
SAN FRANCISCO
PITTSBURG
SAN RAFAEL
CONCORD
RODEO
MARTINEZ
HERCULES
SAN GERONIMO
LAGUNITAS
ALAMEDA
ANTIOCH
SAN ANSELMO
BRENTWOOD
SAN FRANCISCO
CONCORD
FAIRFAX
WOODACRE
FOREST KNOLLS
WALNUT CREEK
PINOLE
RICHMOND
CONCORD
SAN PABLO
SAN RAFAEL
ANTIOCH
EL SOBRANTE
OAKLAND
PLEASANT HILL
CONCORD
GREENBRAE
SAN FRANCISCO
LAFAYETTE
CLAYTON
RICHMOND
RICHMOND
LARKSPUR
SAN QUENTIN
EL CERRITO
CORTE MADERA
WALNUT CREEK
BERKELEY
SAN FRANCISCO
MILL VALLEY
ORINDA
BERKELEY
BERKELEY
BYRON
STINSON BEACH
ALBANY
BERKELEY
SAN FRANCISCO
WALNUT CREEK
BERKELEY
BERKELEY
BERKELEY
ALAMO
BERKELEY
SAUSALITO
MORAGA
BELVEDERE TIBURON
SAN FRANCISCO
BERKELEY
OAKLAND
OAKLAND
OAKLAND
LIVERMORE
EMERYVILLE
DIABLO
DANVILLE
DANVILLE
SAN FRANCISCO
OAKLAND
SAN FRANCISCO
OAKLAND
SAN RAMON
OAKLAND
OAKLAND
CASTRO VALLEY
SAN FRANCISCO
SAN FRANCISC

Location  City Latitude  City Longitude                     Venue  \
0      NAPA      38.410697     -122.298535            Regusci Winery   
1      NAPA      38.410697     -122.298535  Stag's Leap Wine Cellars   
2      NAPA      38.410697     -122.298535        Clos Du Val Winery   
3      NAPA      38.410697     -122.298535         Stags' Leap Manor   
4      NAPA      38.410697     -122.298535      Pine Ridge Vineyards   
5      NAPA      38.410697     -122.298535       Chimney Rock Winery   
6      NAPA      38.410697     -122.298535  Robert Sinskey Vineyards   
7      NAPA      38.410697     -122.298535      Cliff Lede Vineyards   
8      NAPA      38.410697     -122.298535       Silverado Vineyards   
9      NAPA      38.410697     -122.298535          Hotel Yountville   
10     NAPA      38.410697     -122.298535                Bardessono   
11     NAPA      38.410697     -122.298535            Bouchon Bakery   
12     NAPA      38.410697     -122.298535                  Paraduxx   
13     NAPA      38.410697     -122.298535           Hagafen Cellars   
14     NAPA      38.410697     -122.298535                   Bouchon   
15     NAPA      38.410697     -122.298535        Villagio Inn & Spa   
16     NAPA      38.410697     -122.298535             Bistro Jeanty   
17     NAPA      38.410697     -122.298535                    ad hoc   
18     NAPA      38.410697     -122.298535     Black Stallion Winery   
19     NAPA      38.410697     -122.298535                   Bottega   

    Venue Latitude  Venue Longitude                 Category  
0        38.397917      -122.313842                   Winery  
1        38.398948      -122.323333                   Winery  
2        38.386832      -122.312684                   Winery  
3        38.414180      -122.321451                 Vineyard  
4        38.405997      -122.331374                 Vineyard  
5        38.390511      -122.313719                   Winery  
6        38.425266      -122.337051                 Wine Bar  
7        38.424207      -122.344516                   Winery  
8        38.412351      -122.337094                 Vineyard  
9        38.398128      -122.357733                    Hotel  
10       38.402940      -122.360310                    Hotel  
11       38.402372      -122.361905                   Bakery  
12       38.437159      -122.351436                   Winery  
13       38.364609      -122.289487                   Winery  
14       38.402576      -122.362074        French Restaurant  
15       38.400129      -122.359762                    Hotel  
16       38.400961      -122.359880        French Restaurant  
17       38.399189      -122.358514  New American Restaurant  
18       38.359855      -122.291358                   Winery  
19       38.401801      -122.362437       Italian Restaurant

In [10]:
bay_venues.rename(columns={'City Latitude':'latitude','City Longitude':'longitude'}, inplace=True)
baydata = pd.merge(bay_venues, data[['ZIP','longitude']], on='longitude')
print("The shape of Bay Area Raw Data extracted through FourSqaure API is {}".format(baydata.shape))
print("There are {} unique neighborhoods according to zip-code and {} unique cities.".format(len(baydata.ZIP.unique()),len(baydata.Location.unique())))
baydata.head()

The shape of Bay Area Raw Data extracted through FourSqaure API is (23536, 8)
There are 249 unique neighborhoods according to zip-code and 99 unique cities.


Location   latitude   longitude                     Venue  Venue Latitude  \
0     NAPA  38.410697 -122.298535            Regusci Winery       38.397917   
1     NAPA  38.410697 -122.298535  Stag's Leap Wine Cellars       38.398948   
2     NAPA  38.410697 -122.298535        Clos Du Val Winery       38.386832   
3     NAPA  38.410697 -122.298535         Stags' Leap Manor       38.414180   
4     NAPA  38.410697 -122.298535      Pine Ridge Vineyards       38.405997   

   Venue Longitude  Category    ZIP  
0      -122.313842    Winery  94558  
1      -122.323333    Winery  94558  
2      -122.312684    Winery  94558  
3      -122.321451  Vineyard  94558  
4      -122.331374  Vineyard  94558

In [12]:
# Backup raw data to csv
baydata.to_csv(r'C:\Users\sywan\Anaconda3\_NoteBook\BayAreaData.csv')

### **Part 3 Create map of Bay Area

In [13]:
# create map of SF Bay Area using latitude and longitude values
import folium
lat_bay  = 37.3872782660371
long_bay = -122.023027702134
map_bay  = folium.Map(location=[lat_bay, long_bay], zoom_start=10)

# add markers to map
for lat, lng, label in zip(data['latitude'], data['longitude'], data['PO_NAME']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_bay)  
    
map_bay

### **Part 4 Analyze Data

In [14]:
# one hot encoding
bay_onehot = pd.get_dummies(baydata[['Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
bay_onehot['Location'] = baydata['Location'] 

# move neighborhood column to the first column
fixed_columns = [bay_onehot.columns[-1]] + list(bay_onehot.columns[:-1])
bay_onehot = bay_onehot[fixed_columns]

bay_onehot.head()

Location  Accessories Store  Afghan Restaurant  Airport  Airport Lounge  \
0     NAPA                  0                  0        0               0   
1     NAPA                  0                  0        0               0   
2     NAPA                  0                  0        0               0   
3     NAPA                  0                  0        0               0   
4     NAPA                  0                  0        0               0   

   American Restaurant  Amphitheater  Animal Shelter  Arcade  \
0                    0             0               0       0   
1                    0             0               0       0   
2                    0             0               0       0   
3                    0             0               0       0   
4                    0             0               0       0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Asian Restaurant  Auditorium  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  \
0                 0           0          0           0       0     0    0   
1                 0           0          0           0       0     0    0   
2                 0           0          0           0       0     0    0   
3                 0           0          0           0       0     0    0   
4                 0           0          0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Stadium  Bath House  Beach  \
0               0                 0                   0           0      0   
1               0                 0                   0           0      0   
2               0                 0                   0           0      0   
3               0                 0                   0           0      0   
4               0                 0                   0           0      0   

   Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  Board Shop  \
0                0         0            0           0           0   
1                0         0            0           0           0   
2                0         0            0           0           0   
3                0         0            0           0           0   
4                0         0            0           0           0   

   Boat or Ferry  Bookstore  Botanical Garden  Boutique  Bowling Alley  \
0              0          0                 0         0              0   
1              0          0                 0         0              0   
2              0          0                 0         0              0   
3              0          0                 0         0              0   
4              0          0                 0         0              0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bubble Tea Shop  Buffet  \
0                     0               0        0                0       0   
1                     0               0        0                0       0   
2                     0               0        0                0       0   
3                     0               0        0                0       0   
4                     0               0        0                0       0   

   Building  Burger Joint  Burmese Restaurant  Burrito Place  Butcher  Café  \
0         0             0                   0              0        0     0   
1         0             0                   0              0        0     0   
2         0             0                   0              0        0     0   
3         0             0                   0              0        0     0   
4         0             0                   0        

In [15]:
#  Grouped Bay Data
baygp = bay_onehot.groupby('Location').mean().reset_index()
baygp.head()

Location  Accessories Store  Afghan Restaurant  Airport  \
0          ALAMEDA                0.0                0.0      0.0   
1            ALAMO                0.0                0.0      0.0   
2           ALBANY                0.0                0.0      0.0   
3           ALVISO                0.0                0.0      0.0   
4  AMERICAN CANYON                0.0                0.0      0.0   

   Airport Lounge  American Restaurant  Amphitheater  Animal Shelter  Arcade  \
0             0.0                  0.0           0.0             0.0    0.05   
1             0.0                  0.1           0.0             0.0    0.00   
2             0.0                  0.0           0.0             0.0    0.00   
3             0.0                  0.0           0.0             0.0    0.00   
4             0.0                  0.0           0.0             0.0    0.00   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                     0.0          0.0         0.0                  0.0   
1                     0.0          0.0         0.0                  0.0   
2                     0.0          0.0         0.0                  0.0   
3                     0.0          0.0         0.0                  0.0   
4                     0.0          0.0         0.0                  0.0   

   Asian Restaurant  Auditorium  BBQ Joint  Bagel Shop  Bakery  Bank    Bar  \
0               0.0         0.0        0.0         0.0   0.025   0.0  0.025   
1               0.0         0.0        0.0         0.0   0.000   0.0  0.000   
2               0.0         0.0        0.0         0.0   0.000   0.0  0.000   
3               0.0         0.0        0.0         0.0   0.000   0.0  0.000   
4               0.0         0.0        0.0         0.0   0.050   0.0  0.000   

   Baseball Field  Baseball Stadium  Basketball Stadium  Bath House  Beach  \
0             0.0               0.0                 0.0         0.0  0.025   
1             0.0               0.0                 0.0         0.0  0.000   
2             0.0               0.0                 0.0         0.0  0.000   
3             0.0               0.0                 0.0         0.0  0.000   
4             0.0               0.0                 0.0         0.0  0.000   

   Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  Board Shop  \
0              0.0       0.0        0.025         0.0         0.0   
1              0.0       0.0        0.000         0.0         0.0   
2              0.0       0.0        0.050         0.0         0.0   
3              0.0       0.0        0.000         0.0         0.0   
4              0.0       0.0        0.000         0.0         0.0   

   Boat or Ferry  Bookstore  Botanical Garden  Boutique  Bowling Alley  \
0            0.0        0.0               0.0       0.0            0.0   
1            0.0        0.0               0.0       0.0            0.0   
2            0.0        0.0               0.0       0.0            0.0   
3            0.0        0.0               0.0       0.0            0.0   
4            0.0        0.0               0.0       0.0            0.0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bubble Tea Shop  Buffet  \
0                   0.0            0.00     0.05              0.0     0.0   
1                   0.0            0.00     0.00              0.0     0.0   
2                   0.0            0.05     0.10              0.0     0.0   
3                   0.0            0.00     0.05              0.0     0.0   
4                   0.0            0.00     0.00              0.0     0.0   

   Building  Burger Joint  Burmese Restaurant  Burrito Place  Butcher   Café  \
0       0.0         0.025               0.025            0.0      0.0  0.025   
1       0.0         0.050               0.000            0.0      0.0  0.050   
2       0.0         0.000               0.000            0.0      0.0  0.050   
3       0.0         0.050               0.000            0.0      0.0  0.000

In [16]:
# Create a mask to filter restaurant
col_ls  = baygp.columns.tolist()
food_ls = ['Location','Restaurant','Steak','Buffet','Food','Pub']
mask    = [False] * len(col_ls)
for item in food_ls:
    temp = [i.find(item)>=0 for i in col_ls]
    mask = [x or y for x, y in zip(mask, temp)]

from itertools import compress
bayfood = baygp[list(compress(col_ls,mask))]
bayfood


Location  Afghan Restaurant  American Restaurant  \
0               ALAMEDA             0.0000             0.000000   
1                 ALAMO             0.0000             0.100000   
2                ALBANY             0.0000             0.000000   
3                ALVISO             0.0000             0.000000   
4       AMERICAN CANYON             0.0000             0.000000   
5               ANTIOCH             0.0250             0.050000   
6              ATHERTON             0.0000             0.000000   
7               BELMONT             0.0500             0.000000   
8     BELVEDERE TIBURON             0.0000             0.000000   
9               BENICIA             0.0000             0.050000   
10             BERKELEY             0.0000             0.000000   
11        BIRDS LANDING             0.0000             0.000000   
12            BRENTWOOD             0.0000             0.050000   
13             BRISBANE             0.0000             0.000000   
14           BURLINGAME             0.0000             0.000000   
15                BYRON             0.0000             0.050000   
16             CAMPBELL             0.0000             0.100000   
17        CASTRO VALLEY             0.0000             0.000000   
18              CLAYTON             0.0000             0.050000   
19              CONCORD             0.0000             0.037500   
20         CORTE MADERA             0.0000             0.050000   
21             CROCKETT             0.0000             0.050000   
22            CUPERTINO             0.0000             0.000000   
23            DALY CITY             0.0000             0.000000   
24             DANVILLE             0.0000             0.100000   
25               DIABLO             0.0000             0.100000   
26                DIXON             0.0000             0.000000   
27               DUBLIN             0.0500             0.000000   
28           EL CERRITO             0.0000             0.000000   
29          EL SOBRANTE             0.0000             0.000000   
30           EMERYVILLE             0.0000             0.000000   
31              FAIRFAX             0.0000             0.000000   
32            FAIRFIELD             0.0000             0.000000   
33        FOREST KNOLLS             0.0000             0.100000   
34              FREMONT             0.0000             0.000000   
35            GREENBRAE             0.0000             0.050000   
36        HALF MOON BAY             0.0000             0.050000   
37              HAYWARD             0.0000             0.025000   
38             HERCULES             0.0000             0.050000   
39            LAFAYETTE             0.0000             0.100000   
40            LAGUNITAS             0.0000             0.150000   
41             LARKSPUR             0.0000             0.150000   
42            LIVERMORE             0.0000             0.052632   
43            LOS ALTOS             0.0000             0.050000   
44             MARTINEZ             0.0000             0.100000   
45           MENLO PARK             0.0000             0.000000   
46          MILL VALLEY             0.0000             0.000000   
47             MILLBRAE             0.0000             0.000000   
48             MILPITAS             0.0000             0.000000   
49               MORAGA             0.0000             0.000000   
50           MOSS BEACH             0.0000             0.000000   
51       MOUNT HAMILTON             0.0000             0.000000   
52        MOUNTAIN VIEW             0.0000             0.050000   
53                 NAPA             0.0000             0.025000   
54               NEWARK             0.0000             0.050000   
55              NICASIO             0.0000             0.150000   
56               NOVATO             0.0000             0.050000   
57              OAKLAND             0.0000             0.007143   
58               OAKLEY             0.0000             0.05000

In [17]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [18]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Location']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
bay_venues_sorted = pd.DataFrame(columns=columns)
bay_venues_sorted['Location'] = bayfood['Location']

for ind in np.arange(baygp.shape[0]):
    bay_venues_sorted.iloc[ind, 1:] = return_most_common_venues(bayfood.iloc[ind, :], num_top_venues)

bay_venues_sorted.head()

Location  1st Most Common Venue          2nd Most Common Venue  \
0          ALAMEDA  Vietnamese Restaurant             Mexican Restaurant   
1            ALAMO    American Restaurant             Italian Restaurant   
2           ALBANY     Tibetan Restaurant  Vegetarian / Vegan Restaurant   
3           ALVISO   Fast Food Restaurant  Vegetarian / Vegan Restaurant   
4  AMERICAN CANYON        Thai Restaurant          Vietnamese Restaurant   

       3rd Most Common Venue     4th Most Common Venue  \
0  Middle Eastern Restaurant        Burmese Restaurant   
1            Thai Restaurant  Mediterranean Restaurant   
2          Korean Restaurant                Food Truck   
3   Mediterranean Restaurant        Mexican Restaurant   
4         Mexican Restaurant      Fast Food Restaurant   

     5th Most Common Venue  6th Most Common Venue 7th Most Common Venue  \
0        German Restaurant     Italian Restaurant      Sushi Restaurant   
1        German Restaurant      Fondue Restaurant                  Food   
2  New American Restaurant  Vietnamese Restaurant     French Restaurant   
3      Filipino Restaurant      Hotpot Restaurant     Health Food Store   
4        Indian Restaurant    Hawaiian Restaurant      Greek Restaurant   

  8th Most Common Venue 9th Most Common Venue  10th Most Common Venue  
0     Hotpot Restaurant   Hawaiian Restaurant        Greek Restaurant  
1            Food Court            Food Truck       French Restaurant  
2     Fondue Restaurant                  Food              Food Court  
3   Hawaiian Restaurant      Greek Restaurant  Gluten-free Restaurant  
4     Health Food Store     Hotpot Restaurant       German Restaurant

In [19]:
# set number of clusters
kclusters = 10

bayfood_clustering = bayfood.drop('Location', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(bayfood_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([2, 1, 3, 3, 0, 2, 9, 3, 3, 9])

In [20]:
# add clustering labels
bay_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

bay_merged = baydata

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
bay_merged = bay_merged.join(bay_venues_sorted.set_index('Location'), on='Location')

bay_merged.head() # check the last columns!

Location   latitude   longitude                     Venue  Venue Latitude  \
0     NAPA  38.410697 -122.298535            Regusci Winery       38.397917   
1     NAPA  38.410697 -122.298535  Stag's Leap Wine Cellars       38.398948   
2     NAPA  38.410697 -122.298535        Clos Du Val Winery       38.386832   
3     NAPA  38.410697 -122.298535         Stags' Leap Manor       38.414180   
4     NAPA  38.410697 -122.298535      Pine Ridge Vineyards       38.405997   

   Venue Longitude  Category    ZIP  Cluster Labels 1st Most Common Venue  \
0      -122.313842    Winery  94558               3     French Restaurant   
1      -122.323333    Winery  94558               3     French Restaurant   
2      -122.312684    Winery  94558               3     French Restaurant   
3      -122.321451  Vineyard  94558               3     French Restaurant   
4      -122.331374  Vineyard  94558               3     French Restaurant   

  2nd Most Common Venue 3rd Most Common Venue    4th Most Common Venue  \
0    Italian Restaurant            Steakhouse  New American Restaurant   
1    Italian Restaurant            Steakhouse  New American Restaurant   
2    Italian Restaurant            Steakhouse  New American Restaurant   
3    Italian Restaurant            Steakhouse  New American Restaurant   
4    Italian Restaurant            Steakhouse  New American Restaurant   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0            Restaurant      Tapas Restaurant   American Restaurant   
1            Restaurant      Tapas Restaurant   American Restaurant   
2            Restaurant      Tapas Restaurant   American Restaurant   
3            Restaurant      Tapas Restaurant   American Restaurant   
4            Restaurant      Tapas Restaurant   American Restaurant   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0      Asian Restaurant   Filipino Restaurant      Health Food Store  
1      Asian Restaurant   Filipino Restaurant      Health Food Store  
2      Asian Restaurant   Filipino Restaurant      Health Food Store  
3      Asian Restaurant   Filipino Restaurant      Health Food Store  
4      Asian Restaurant   Filipino Restaurant      Health Food Store

In [ ]:
# create map
map_clusters = folium.Map(location=[lat_bay, long_bay], zoom_start=10)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(bay_merged['latitude'], bay_merged['longitude'], bay_merged['Location'], bay_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

### Examine the clusters

In [21]:
bay_merged.loc[bay_merged['Cluster Labels'] == 0]

Location   latitude   longitude  \
140   AMERICAN CANYON  38.182079 -122.247359   
141   AMERICAN CANYON  38.182079 -122.247359   
142   AMERICAN CANYON  38.182079 -122.247359   
143   AMERICAN CANYON  38.182079 -122.247359   
144   AMERICAN CANYON  38.182079 -122.247359   
145   AMERICAN CANYON  38.182079 -122.247359   
146   AMERICAN CANYON  38.182079 -122.247359   
147   AMERICAN CANYON  38.182079 -122.247359   
148   AMERICAN CANYON  38.182079 -122.247359   
149   AMERICAN CANYON  38.182079 -122.247359   
150   AMERICAN CANYON  38.182079 -122.247359   
151   AMERICAN CANYON  38.182079 -122.247359   
152   AMERICAN CANYON  38.182079 -122.247359   
153   AMERICAN CANYON  38.182079 -122.247359   
154   AMERICAN CANYON  38.182079 -122.247359   
155   AMERICAN CANYON  38.182079 -122.247359   
156   AMERICAN CANYON  38.182079 -122.247359   
157   AMERICAN CANYON  38.182079 -122.247359   
158   AMERICAN CANYON  38.182079 -122.247359   
159   AMERICAN CANYON  38.182079 -122.247359   
2532           DUBLIN  37.714873 -121.927009   
2533           DUBLIN  37.714873 -121.927009   
2534           DUBLIN  37.714873 -121.927009   
2535           DUBLIN  37.714873 -121.927009   
2536           DUBLIN  37.714873 -121.927009   
2537           DUBLIN  37.714873 -121.927009   
2538           DUBLIN  37.714873 -121.927009   
2539           DUBLIN  37.714873 -121.927009   
2540           DUBLIN  37.714873 -121.927009   
2541           DUBLIN  37.714873 -121.927009   
2542           DUBLIN  37.714873 -121.927009   
2543           DUBLIN  37.714873 -121.927009   
2544           DUBLIN  37.714873 -121.927009   
2545           DUBLIN  37.714873 -121.927009   
2546           DUBLIN  37.714873 -121.927009   
2547           DUBLIN  37.714873 -121.927009   
2548           DUBLIN  37.714873 -121.927009   
2549           DUBLIN  37.714873 -121.927009   
2550           DUBLIN  37.714873 -121.927009   
2551           DUBLIN  37.714873 -121.927009   
2652      SAN LORENZO  37.681258 -122.128088   
2653      SAN LORENZO  37.681258 -122.128088   
2654      SAN LORENZO  37.681258 -122.128088   
2655      SAN LORENZO  37.681258 -122.128088   
2656      SAN LORENZO  37.681258 -122.128088   
2657      SAN LORENZO  37.681258 -122.128088   
2658      SAN LORENZO  37.681258 -122.128088   
2659      SAN LORENZO  37.681258 -122.128088   
2660      SAN LORENZO  37.681258 -122.128088   
2661      SAN LORENZO  37.681258 -122.128088   
2662      SAN LORENZO  37.681258 -122.128088   
2663      SAN LORENZO  37.681258 -122.128088   
2664      SAN LORENZO  37.681258 -122.128088   
2665      SAN LORENZO  37.681258 -122.128088   
2666      SAN LORENZO  37.681258 -122.128088   
2667      SAN LORENZO  37.681258 -122.128088   
2668      SAN LORENZO  37.681258 -122.128088   
2669      SAN LORENZO  37.681258 -122.128088   
2670      SAN LORENZO  37.681258 -122.128088   
2671      SAN LORENZO  37.681258 -122.128088   
3132           NEWARK  37.521628 -122.044664   
3133           NEWARK  37.521628 -122.044664   
3134           NEWARK  37.521628 -122.044664   
3135           NEWARK  37.521628 -122.044664   
3136           NEWARK  37.521628 -122.044664   
3137           NEWARK  37.521628 -122.044664   
3138           NEWARK  37.521628 -122.044664   
3139           NEWARK  37.521628 -122.044664   
3140           NEWARK  37.521628 -122.044664   
3141           NEWARK  37.521628 -122.044664   
3142           NEWARK  37.521628 -122.044664   
3143           NEWARK  37.521628 -122.044664   
3144           NEWARK  37.521628 -122.044664   
3145           NEWARK  37.521628 -122.044664   
3146           NEWARK  37.521628 -122.044664   
3147           NEWARK  37.521628 -122.044664   
3148           NEWARK  37.521628 -122.044664   
3149           NEWARK  37.521628 -122.044664   
3150           NEWARK  37.521628 -122.044664   
3151           NEWARK  37.521628 -122.044664   

                                     Venue  Venue Latitude  Venue Longitude  \
140                                Dunkin'   

In [22]:
bay_merged.loc[bay_merged['Cluster Labels'] == 1]

Location   latitude   longitude  \
406       SUISUN CITY  38.150717 -122.020761   
407       SUISUN CITY  38.150717 -122.020761   
408       SUISUN CITY  38.150717 -122.020761   
409       SUISUN CITY  38.150717 -122.020761   
410       SUISUN CITY  38.150717 -122.020761   
411       SUISUN CITY  38.150717 -122.020761   
412       SUISUN CITY  38.150717 -122.020761   
1033        LAFAYETTE  37.901570 -122.113683   
1034        LAFAYETTE  37.901570 -122.113683   
1035        LAFAYETTE  37.901570 -122.113683   
1036        LAFAYETTE  37.901570 -122.113683   
1037        LAFAYETTE  37.901570 -122.113683   
1038        LAFAYETTE  37.901570 -122.113683   
1039        LAFAYETTE  37.901570 -122.113683   
1040        LAFAYETTE  37.901570 -122.113683   
1041        LAFAYETTE  37.901570 -122.113683   
1042        LAFAYETTE  37.901570 -122.113683   
1043        LAFAYETTE  37.901570 -122.113683   
1044        LAFAYETTE  37.901570 -122.113683   
1045        LAFAYETTE  37.901570 -122.113683   
1046        LAFAYETTE  37.901570 -122.113683   
1047        LAFAYETTE  37.901570 -122.113683   
1048        LAFAYETTE  37.901570 -122.113683   
1049        LAFAYETTE  37.901570 -122.113683   
1050        LAFAYETTE  37.901570 -122.113683   
1051        LAFAYETTE  37.901570 -122.113683   
1052        LAFAYETTE  37.901570 -122.113683   
1513            ALAMO  37.856373 -122.001410   
1514            ALAMO  37.856373 -122.001410   
1515            ALAMO  37.856373 -122.001410   
1516            ALAMO  37.856373 -122.001410   
1517            ALAMO  37.856373 -122.001410   
1518            ALAMO  37.856373 -122.001410   
1519            ALAMO  37.856373 -122.001410   
1520            ALAMO  37.856373 -122.001410   
1521            ALAMO  37.856373 -122.001410   
1522            ALAMO  37.856373 -122.001410   
1523            ALAMO  37.856373 -122.001410   
1524            ALAMO  37.856373 -122.001410   
1525            ALAMO  37.856373 -122.001410   
1526            ALAMO  37.856373 -122.001410   
1527            ALAMO  37.856373 -122.001410   
1528            ALAMO  37.856373 -122.001410   
1529            ALAMO  37.856373 -122.001410   
1530            ALAMO  37.856373 -122.001410   
1531            ALAMO  37.856373 -122.001410   
1532            ALAMO  37.856373 -122.001410   
1752           DIABLO  37.840273 -121.963502   
1753           DIABLO  37.840273 -121.963502   
1754           DIABLO  37.840273 -121.963502   
1755           DIABLO  37.840273 -121.963502   
1756           DIABLO  37.840273 -121.963502   
1757           DIABLO  37.840273 -121.963502   
1758           DIABLO  37.840273 -121.963502   
1759           DIABLO  37.840273 -121.963502   
1760           DIABLO  37.840273 -121.963502   
1761           DIABLO  37.840273 -121.963502   
1762           DIABLO  37.840273 -121.963502   
1763           DIABLO  37.840273 -121.963502   
1764           DIABLO  37.840273 -121.963502   
1765           DIABLO  37.840273 -121.963502   
1766           DIABLO  37.840273 -121.963502   
1767           DIABLO  37.840273 -121.963502   
1768           DIABLO  37.840273 -121.963502   
1769           DIABLO  37.840273 -121.963502   
1770           DIABLO  37.840273 -121.963502   
1771           DIABLO  37.840273 -121.963502   
1772         DANVILLE  37.817712 -121.986279   
1773         DANVILLE  37.817712 -121.986279   
1774         DANVILLE  37.817712 -121.986279   
1775         DANVILLE  37.817712 -121.986279   
1776         DANVILLE  37.817712 -121.986279   
1777         DANVILLE  37.817712 -121.986279   
1778         DANVILLE  37.817712 -121.986279   
1779         DANVILLE  37.817712 -121.986279   
1780         DANVILLE  37.817712 -121.986279   
1781         DANVILLE  37.817712 -121.986279   
1782         DANVILLE  37.817712 -121.986279   
1783         DANVILLE  37.817712 -121.986279   
1784         DANVILLE  37.817712 -121.986279   
1785         DANVILLE  37.817712 -121.986279   
1786         DANVILLE  37.817712 -121.986279   
1787         DANVILLE  37.817

In [23]:
bay_merged.loc[bay_merged['Cluster Labels'] == 2]

Location   latitude   longitude  \
20      FAIRFIELD  38.279137 -122.025948   
21      FAIRFIELD  38.279137 -122.025948   
22      FAIRFIELD  38.279137 -122.025948   
23      FAIRFIELD  38.279137 -122.025948   
24      FAIRFIELD  38.279137 -122.025948   
25      FAIRFIELD  38.279137 -122.025948   
26      FAIRFIELD  38.279137 -122.025948   
27      FAIRFIELD  38.279137 -122.025948   
28      FAIRFIELD  38.279137 -122.025948   
29      FAIRFIELD  38.279137 -122.025948   
30      FAIRFIELD  38.279137 -122.025948   
31      FAIRFIELD  38.279137 -122.025948   
32      FAIRFIELD  38.279137 -122.025948   
33      FAIRFIELD  38.279137 -122.025948   
34      FAIRFIELD  38.279137 -122.025948   
35      FAIRFIELD  38.279137 -122.025948   
36      FAIRFIELD  38.279137 -122.025948   
37      FAIRFIELD  38.279137 -122.025948   
38      FAIRFIELD  38.279137 -122.025948   
39      FAIRFIELD  38.279137 -122.025948   
206       VALLEJO  38.109064 -122.204057   
207       VALLEJO  38.109064 -122.204057   
208       VALLEJO  38.109064 -122.204057   
209       VALLEJO  38.109064 -122.204057   
210       VALLEJO  38.109064 -122.204057   
211       VALLEJO  38.109064 -122.204057   
212       VALLEJO  38.109064 -122.204057   
213       VALLEJO  38.109064 -122.204057   
214       VALLEJO  38.109064 -122.204057   
215       VALLEJO  38.109064 -122.204057   
216       VALLEJO  38.109064 -122.204057   
217       VALLEJO  38.109064 -122.204057   
218       VALLEJO  38.109064 -122.204057   
219       VALLEJO  38.109064 -122.204057   
220       VALLEJO  38.109064 -122.204057   
221       VALLEJO  38.109064 -122.204057   
222       VALLEJO  38.109064 -122.204057   
223       VALLEJO  38.109064 -122.204057   
224       VALLEJO  38.109064 -122.204057   
225       VALLEJO  38.109064 -122.204057   
246       VALLEJO  38.130289 -122.298021   
247       VALLEJO  38.130289 -122.298021   
248       VALLEJO  38.130289 -122.298021   
249       VALLEJO  38.130289 -122.298021   
250       VALLEJO  38.130289 -122.298021   
251       VALLEJO  38.130289 -122.298021   
252       VALLEJO  38.130289 -122.298021   
253       VALLEJO  38.130289 -122.298021   
254       VALLEJO  38.130289 -122.298021   
255       VALLEJO  38.130289 -122.298021   
256       VALLEJO  38.130289 -122.298021   
257       VALLEJO  38.130289 -122.298021   
258       VALLEJO  38.130289 -122.298021   
259       VALLEJO  38.130289 -122.298021   
260       VALLEJO  38.130289 -122.298021   
261       VALLEJO  38.130289 -122.298021   
262       VALLEJO  38.130289 -122.298021   
263       VALLEJO  38.130289 -122.298021   
264       VALLEJO  38.130289 -122.298021   
265       VALLEJO  38.130289 -122.298021   
266       VALLEJO  38.138542 -122.254380   
267       VALLEJO  38.138542 -122.254380   
268       VALLEJO  38.138542 -122.254380   
269       VALLEJO  38.138542 -122.254380   
270       VALLEJO  38.138542 -122.254380   
271       VALLEJO  38.138542 -122.254380   
272       VALLEJO  38.138542 -122.254380   
273       VALLEJO  38.138542 -122.254380   
274       VALLEJO  38.138542 -122.254380   
275       VALLEJO  38.138542 -122.254380   
276       VALLEJO  38.138542 -122.254380   
277       VALLEJO  38.138542 -122.254380   
278       VALLEJO  38.138542 -122.254380   
279       VALLEJO  38.138542 -122.254380   
280       VALLEJO  38.138542 -122.254380   
281       VALLEJO  38.138542 -122.254380   
282       VALLEJO  38.138542 -122.254380   
283       VALLEJO  38.138542 -122.254380   
284       VALLEJO  38.138542 -122.254380   
285       VALLEJO  38.138542 -122.254380   
306       VALLEJO  38.098477 -122.244162   
307       VALLEJO  38.098477 -122.244162   
308       VALLEJO  38.098477 -122.244162   
309       VALLEJO  38.098477 -122.244162   
310       VALLEJO  38.098477 -122.244162   
311       VALLEJO  38.098477 -122.244162   
312       VALLEJO  38.098477 -122.244162   
313       VALLEJO  38.098477 -122.244162   
314       VALLEJO  38.098477 -122.244162   
315       VALLEJO  38.098477 -122.244162   
316  

In [24]:
bay_merged.loc[bay_merged['Cluster Labels'] == 3]

Location   latitude   longitude  \
0                  NAPA  38.410697 -122.298535   
1                  NAPA  38.410697 -122.298535   
2                  NAPA  38.410697 -122.298535   
3                  NAPA  38.410697 -122.298535   
4                  NAPA  38.410697 -122.298535   
5                  NAPA  38.410697 -122.298535   
6                  NAPA  38.410697 -122.298535   
7                  NAPA  38.410697 -122.298535   
8                  NAPA  38.410697 -122.298535   
9                  NAPA  38.410697 -122.298535   
10                 NAPA  38.410697 -122.298535   
11                 NAPA  38.410697 -122.298535   
12                 NAPA  38.410697 -122.298535   
13                 NAPA  38.410697 -122.298535   
14                 NAPA  38.410697 -122.298535   
15                 NAPA  38.410697 -122.298535   
16                 NAPA  38.410697 -122.298535   
17                 NAPA  38.410697 -122.298535   
18                 NAPA  38.410697 -122.298535   
19                 NAPA  38.410697 -122.298535   
40                DIXON  38.434585 -121.781528   
41                DIXON  38.434585 -121.781528   
42                DIXON  38.434585 -121.781528   
43                DIXON  38.434585 -121.781528   
44                DIXON  38.434585 -121.781528   
45                DIXON  38.434585 -121.781528   
46                DIXON  38.434585 -121.781528   
47                DIXON  38.434585 -121.781528   
48                DIXON  38.434585 -121.781528   
49                DIXON  38.434585 -121.781528   
50                DIXON  38.434585 -121.781528   
51                DIXON  38.434585 -121.781528   
52                DIXON  38.434585 -121.781528   
53                DIXON  38.434585 -121.781528   
54                DIXON  38.434585 -121.781528   
55                DIXON  38.434585 -121.781528   
56                DIXON  38.434585 -121.781528   
57                DIXON  38.434585 -121.781528   
58                DIXON  38.434585 -121.781528   
59                DIXON  38.434585 -121.781528   
80                 NAPA  38.266265 -122.311414   
81                 NAPA  38.266265 -122.311414   
82                 NAPA  38.266265 -122.311414   
83                 NAPA  38.266265 -122.311414   
84                 NAPA  38.266265 -122.311414   
85                 NAPA  38.266265 -122.311414   
86                 NAPA  38.266265 -122.311414   
87                 NAPA  38.266265 -122.311414   
88                 NAPA  38.266265 -122.311414   
89                 NAPA  38.266265 -122.311414   
90                 NAPA  38.266265 -122.311414   
91                 NAPA  38.266265 -122.311414   
92                 NAPA  38.266265 -122.311414   
93                 NAPA  38.266265 -122.311414   
94                 NAPA  38.266265 -122.311414   
95                 NAPA  38.266265 -122.311414   
96                 NAPA  38.266265 -122.311414   
97                 NAPA  38.266265 -122.311414   
98                 NAPA  38.266265 -122.311414   
99                 NAPA  38.266265 -122.311414   
200       BIRDS LANDING  38.145878 -121.865551   
201       BIRDS LANDING  38.145878 -121.865551   
202       BIRDS LANDING  38.145878 -121.865551   
203       BIRDS LANDING  38.145878 -121.865551   
204       BIRDS LANDING  38.145878 -121.865551   
205       BIRDS LANDING  38.145878 -121.865551   
413       SAN FRANCISCO  37.772961 -122.410672   
414       SAN FRANCISCO  37.772961 -122.410672   
415       SAN FRANCISCO  37.772961 -122.410672   
416       SAN FRANCISCO  37.772961 -122.410672   
417       SAN FRANCISCO  37.772961 -122.410672   
418       SAN FRANCISCO  37.772961 -122.410672   
419       SAN FRANCISCO  37.772961 -122.410672   
420       SAN FRANCISCO  37.772961 -122.410672   
421       SAN FRANCISCO  37.772961 -122.410672   
422       SAN FRANCISCO  37.772961 -122.410672   
423       SAN FRANCISCO  37.772961 -122.410672   
424       SAN FRANCISCO  37.772961 -122.410672   
425       SAN FRANCISCO  37.772961 -122.410672   
426       SAN F

In [25]:
bay_merged.loc[bay_merged['Cluster Labels'] == 4]

Location   latitude   longitude  \
366        CROCKETT  38.047533 -122.224054   
367        CROCKETT  38.047533 -122.224054   
368        CROCKETT  38.047533 -122.224054   
369        CROCKETT  38.047533 -122.224054   
370        CROCKETT  38.047533 -122.224054   
371        CROCKETT  38.047533 -122.224054   
372        CROCKETT  38.047533 -122.224054   
373        CROCKETT  38.047533 -122.224054   
374        CROCKETT  38.047533 -122.224054   
375        CROCKETT  38.047533 -122.224054   
376        CROCKETT  38.047533 -122.224054   
377        CROCKETT  38.047533 -122.224054   
378        CROCKETT  38.047533 -122.224054   
379        CROCKETT  38.047533 -122.224054   
380        CROCKETT  38.047533 -122.224054   
381        CROCKETT  38.047533 -122.224054   
382        CROCKETT  38.047533 -122.224054   
383        CROCKETT  38.047533 -122.224054   
384        CROCKETT  38.047533 -122.224054   
385        CROCKETT  38.047533 -122.224054   
386      PORT COSTA  38.045259 -122.190863   
387      PORT COSTA  38.045259 -122.190863   
388      PORT COSTA  38.045259 -122.190863   
389      PORT COSTA  38.045259 -122.190863   
390      PORT COSTA  38.045259 -122.190863   
391      PORT COSTA  38.045259 -122.190863   
392      PORT COSTA  38.045259 -122.190863   
393      PORT COSTA  38.045259 -122.190863   
394      PORT COSTA  38.045259 -122.190863   
395      PORT COSTA  38.045259 -122.190863   
396      PORT COSTA  38.045259 -122.190863   
397      PORT COSTA  38.045259 -122.190863   
398      PORT COSTA  38.045259 -122.190863   
399      PORT COSTA  38.045259 -122.190863   
400      PORT COSTA  38.045259 -122.190863   
401      PORT COSTA  38.045259 -122.190863   
402      PORT COSTA  38.045259 -122.190863   
403      PORT COSTA  38.045259 -122.190863   
404      PORT COSTA  38.045259 -122.190863   
405      PORT COSTA  38.045259 -122.190863   
493           RODEO  38.036397 -122.252708   
494           RODEO  38.036397 -122.252708   
495           RODEO  38.036397 -122.252708   
496           RODEO  38.036397 -122.252708   
497           RODEO  38.036397 -122.252708   
498           RODEO  38.036397 -122.252708   
499           RODEO  38.036397 -122.252708   
500           RODEO  38.036397 -122.252708   
501           RODEO  38.036397 -122.252708   
502           RODEO  38.036397 -122.252708   
503           RODEO  38.036397 -122.252708   
504           RODEO  38.036397 -122.252708   
505           RODEO  38.036397 -122.252708   
506           RODEO  38.036397 -122.252708   
507           RODEO  38.036397 -122.252708   
508           RODEO  38.036397 -122.252708   
509           RODEO  38.036397 -122.252708   
510           RODEO  38.036397 -122.252708   
511           RODEO  38.036397 -122.252708   
512           RODEO  38.036397 -122.252708   
533        HERCULES  38.010752 -122.267296   
534        HERCULES  38.010752 -122.267296   
535        HERCULES  38.010752 -122.267296   
536        HERCULES  38.010752 -122.267296   
537        HERCULES  38.010752 -122.267296   
538        HERCULES  38.010752 -122.267296   
539        HERCULES  38.010752 -122.267296   
540        HERCULES  38.010752 -122.267296   
541        HERCULES  38.010752 -122.267296   
542        HERCULES  38.010752 -122.267296   
543        HERCULES  38.010752 -122.267296   
544        HERCULES  38.010752 -122.267296   
545        HERCULES  38.010752 -122.267296   
546        HERCULES  38.010752 -122.267296   
547        HERCULES  38.010752 -122.267296   
548        HERCULES  38.010752 -122.267296   
549        HERCULES  38.010752 -122.267296   
550        HERCULES  38.010752 -122.267296   
551        HERCULES  38.010752 -122.267296   
552        HERCULES  38.010752 -122.267296   
1173   CORTE MADERA  37.925416 -122.515070   
1174   CORTE MADERA  37.925416 -122.515070   
1175   CORTE MADERA  37.925416 -122.515070   
1176   CORTE MADERA  37.925416 -122.515070   
1177   CORTE MADERA  37.925416 -122.515070   
1178   CORTE MADERA  37.925416 -122.515070   
1179   CO

In [ ]:
bay_merged.loc[bay_merged['Cluster Labels'] == 0,bay_merged.columns[[1] + list(range(5, bay_merged.shape[1]))]]

In [ ]:
bay_merged.loc[bay_merged['Cluster Labels'] == 1, bay_merged.columns[[1] + list(range(5, bay_merged.shape[1]))]]

In [ ]:
bay_merged.loc[bay_merged['Cluster Labels'] == 2, bay_merged.columns[[1] + list(range(5, bay_merged.shape[1]))]]

In [ ]:
bay_merged.loc[bay_merged['Cluster Labels'] == 3, bay_merged.columns[[1] + list(range(5, bay_merged.shape[1]))]]

In [ ]:
bay_merged.loc[bay_merged['Cluster Labels'] == 4, bay_merged.columns[[1] + list(range(5, bay_merged.shape[1]))]]

#### Conclusions:
Now, we can examine each cluster and determine the discriminating venue categories that distinguish each cluster. Based on the defining categories, here are the cluster name and its category:
- Cluster 0: Coffee, Food and General Stores
- Cluster 1: Trasnportation (Bus Line)
- Cluster 2: Pool
- Cluster 3: Park
- Cluster 4: Other Restaurant